#라이브러리

In [9]:
import pandas as pd
import numpy as np
import os
import tensorflow as tf
from sklearn.model_selection import train_test_split
from pandas_profiling import ProfileReport
from sklearn.preprocessing import StandardScaler
import kerastuner as kt
import IPython

np.random.seed(3)
tf.random.set_seed(3)

#데이터 불러오기

In [34]:
df = pd.read_csv('ocdd.csv')
df

matchId       champ1       champ2       champ3       champ4  \
0        KR_5551835474         Sett     Volibear        Sylas      Caitlyn   
1        KR_5548658817        Riven       Graves  TwistedFate       Ezreal   
2        KR_5559966199        Poppy          Zac       Qiyana         Jinx   
3        KR_5559990988        Riven        Shaco     Renekton       Twitch   
4        KR_5559888855  Mordekaiser          Zac       Qiyana       Samira   
...                ...          ...          ...          ...          ...   
131089  KR_5558452736R        Jayce        Talon      Orianna  MissFortune   
131090  KR_5550342411R       Kennen        Viego    Lissandra       Ezreal   
131091  KR_5554890959R       Irelia      XinZhao       Thresh       Ezreal   
131092  KR_5554378311R         Ekko  TwistedFate         Jhin        Garen   
131093  KR_5556957768R         Shen      Leblanc        Viego   Blitzcrank   

            champ5    champ6    champ7       champ8       champ9     champ10  \
0       Blitzcrank  Malphite    LeeSin       Veigar  MissFortune       Amumu   
1          Morgana     Xayah     Viego          Vex          Jax  Blitzcrank   
2         Nautilus  Volibear  JarvanIV        Sylas     Tristana       Yuumi   
3           Anivia     Jayce      Pyke       Qiyana   Cassiopeia         Zac   
4           Maokai     Viego    Lillia  TwistedFate        Vayne        Pyke   
...            ...       ...       ...          ...          ...         ...   
131089      Thresh    Irelia      Ekko     Vladimir       Lucian  Blitzcrank   
131090        Pyke       Jax    LeeSin      Leblanc      Caitlyn       Shaco   
131091       Sylas    Darius    Graves       Zilean        Vayne        Sett   
131092        Pyke     Riven  JarvanIV         Ahri        Ziggs       Yuumi   
131093      Ezreal  Renekton   Caitlyn           Vi         Ahri       Leona   

        win  
0         1  
1         1  
2         1  
3         0  
4         1  
...     ...  
131089    0  
131090    0  
131091    0  
131092    1  
131093    0  

[131094 rows x 12 columns]

In [35]:
df=df[:65547]
df=df.drop(columns='matchId')
target = df['win']
feature = df.drop('win', axis=1)

#인코딩

In [36]:
cList=[]
for i in feature:
    cList = cList + list(feature[i].unique())
cList=sorted(list(set(cList)))
len(cList)

157

In [59]:
cDict={}
n=0
for i in cList:
    temp=str(bin(n))[2:]
    l = 8-len(temp)
    if l !=0:
        temp=str(10**l-1).replace('9','0')+temp
    cDict[i]=temp
    n+=1
cDict

{'Aatrox': '00000000',
 'Ahri': '00000001',
 'Akali': '00000010',
 'Akshan': '00000011',
 'Alistar': '00000100',
 'Amumu': '00000101',
 'Anivia': '00000110',
 'Annie': '00000111',
 'Aphelios': '00001000',
 'Ashe': '00001001',
 'AurelionSol': '00001010',
 'Azir': '00001011',
 'Bard': '00001100',
 'Blitzcrank': '00001101',
 'Brand': '00001110',
 'Braum': '00001111',
 'Caitlyn': '00010000',
 'Camille': '00010001',
 'Cassiopeia': '00010010',
 'Chogath': '00010011',
 'Corki': '00010100',
 'Darius': '00010101',
 'Diana': '00010110',
 'DrMundo': '00010111',
 'Draven': '00011000',
 'Ekko': '00011001',
 'Elise': '00011010',
 'Evelynn': '00011011',
 'Ezreal': '00011100',
 'FiddleSticks': '00011101',
 'Fiora': '00011110',
 'Fizz': '00011111',
 'Galio': '00100000',
 'Gangplank': '00100001',
 'Garen': '00100010',
 'Gnar': '00100011',
 'Gragas': '00100100',
 'Graves': '00100101',
 'Gwen': '00100110',
 'Hecarim': '00100111',
 'Heimerdinger': '00101000',
 'Illaoi': '00101001',
 'Irelia': '00101010',
 

In [60]:
feature = feature.applymap(lambda x: cDict[x])
feature

champ1    champ2    champ3    champ4    champ5    champ6    champ7  \
0      01101011  10001110  01110110  00010000  00001101  01000111  01000000   
1      01100100  00100101  10000001  00011100  01001110  10010000  10001011   
2      01011010  10010111  01011100  00110001  01010001  10001110  00101101   
3      01100100  01101100  01100010  10000010  00000110  00101111  01011011   
4      01001101  10010111  01011100  01100111  01001001  10001011  01000010   
...         ...       ...       ...       ...       ...       ...       ...   
65542  00101010  00011001  10001101  01000100  00001101  00101111  01111010   
65543  00101110  01000000  00111111  00010000  01101100  00111010  10001011   
65544  00010101  00100101  10011010  10000110  01101011  00101010  10010010   
65545  01100100  00101101  00000001  10011001  10010110  00011001  10000001   
65546  01100010  00010000  10001010  00000001  01000001  01101101  00111111   

         champ8    champ9   champ10  
0      10000111  01001011  00000101  
1      10001001  00101110  00001101  
2      01110110  01111110  10010110  
3      01011100  00010010  10010111  
4      10000001  10000110  01011011  
...         ...       ...       ...  
65542  01010111  01001011  01111101  
65543  01000011  00011100  01011011  
65544  01111101  00011100  01110110  
65545  00110000  00100010  01011011  
65546  10001011  00001101  00011100  

[65547 rows x 10 columns]

In [61]:
for i in range(1,11):
    for j in range(8):
        feature[f'c{i}_{j}'] = feature[f'champ{i}'].map(lambda x: int(x[j]))
feature

champ1    champ2    champ3    champ4    champ5    champ6    champ7  \
0      01101011  10001110  01110110  00010000  00001101  01000111  01000000   
1      01100100  00100101  10000001  00011100  01001110  10010000  10001011   
2      01011010  10010111  01011100  00110001  01010001  10001110  00101101   
3      01100100  01101100  01100010  10000010  00000110  00101111  01011011   
4      01001101  10010111  01011100  01100111  01001001  10001011  01000010   
...         ...       ...       ...       ...       ...       ...       ...   
65542  00101010  00011001  10001101  01000100  00001101  00101111  01111010   
65543  00101110  01000000  00111111  00010000  01101100  00111010  10001011   
65544  00010101  00100101  10011010  10000110  01101011  00101010  10010010   
65545  01100100  00101101  00000001  10011001  10010110  00011001  10000001   
65546  01100010  00010000  10001010  00000001  01000001  01101101  00111111   

         champ8    champ9   champ10  ...  c9_6  c9_7  c10_0  c10_1  c10_2  \
0      10000111  01001011  00000101  ...     1     1      0      0      0   
1      10001001  00101110  00001101  ...     1     0      0      0      0   
2      01110110  01111110  10010110  ...     1     0      1      0      0   
3      01011100  00010010  10010111  ...     1     0      1      0      0   
4      10000001  10000110  01011011  ...     1     0      0      1      0   
...         ...       ...       ...  ...   ...   ...    ...    ...    ...   
65542  01010111  01001011  01111101  ...     1     1      0      1      1   
65543  01000011  00011100  01011011  ...     0     0      0      1      0   
65544  01111101  00011100  01110110  ...     0     0      0      1      1   
65545  00110000  00100010  01011011  ...     1     0      0      1      0   
65546  10001011  00001101  00011100  ...     0     1      0      0      0   

       c10_3  c10_4  c10_5  c10_6  c10_7  
0          0      0      1      0      1  
1          0      1      1      0      1  
2          1      0      1      1      0  
3          1      0      1      1      1  
4          1      1      0      1      1  
...      ...    ...    ...    ...    ...  
65542      1      1      1      0      1  
65543      1      1      0      1      1  
65544      1      0      1      1      0  
65545      1      1      0      1      1  
65546      1      1      1      0      0  

[65547 rows x 90 columns]

In [62]:
for i in range(1,11):
    feature=feature.drop(columns=f'champ{i}')
feature

c1_0  c1_1  c1_2  c1_3  c1_4  c1_5  c1_6  c1_7  c2_0  c2_1  ...  c9_6  \
0         0     1     1     0     1     0     1     1     1     0  ...     1   
1         0     1     1     0     0     1     0     0     0     0  ...     1   
2         0     1     0     1     1     0     1     0     1     0  ...     1   
3         0     1     1     0     0     1     0     0     0     1  ...     1   
4         0     1     0     0     1     1     0     1     1     0  ...     1   
...     ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
65542     0     0     1     0     1     0     1     0     0     0  ...     1   
65543     0     0     1     0     1     1     1     0     0     1  ...     0   
65544     0     0     0     1     0     1     0     1     0     0  ...     0   
65545     0     1     1     0     0     1     0     0     0     0  ...     1   
65546     0     1     1     0     0     0     1     0     0     0  ...     0   

       c9_7  c10_0  c10_1  c10_2  c10_3  c10_4  c10_5  c10_6  c10_7  
0         1      0      0      0      0      0      1      0      1  
1         0      0      0      0      0      1      1      0      1  
2         0      1      0      0      1      0      1      1      0  
3         0      1      0      0      1      0      1      1      1  
4         0      0      1      0      1      1      0      1      1  
...     ...    ...    ...    ...    ...    ...    ...    ...    ...  
65542     1      0      1      1      1      1      1      0      1  
65543     0      0      1      0      1      1      0      1      1  
65544     0      0      1      1      1      0      1      1      0  
65545     0      0      1      0      1      1      0      1      1  
65546     1      0      0      0      1      1      1      0      0  

[65547 rows x 80 columns]

In [63]:
df = pd.concat([feature,target],axis=1)
df

c1_0  c1_1  c1_2  c1_3  c1_4  c1_5  c1_6  c1_7  c2_0  c2_1  ...  c9_7  \
0         0     1     1     0     1     0     1     1     1     0  ...     1   
1         0     1     1     0     0     1     0     0     0     0  ...     0   
2         0     1     0     1     1     0     1     0     1     0  ...     0   
3         0     1     1     0     0     1     0     0     0     1  ...     0   
4         0     1     0     0     1     1     0     1     1     0  ...     0   
...     ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
65542     0     0     1     0     1     0     1     0     0     0  ...     1   
65543     0     0     1     0     1     1     1     0     0     1  ...     0   
65544     0     0     0     1     0     1     0     1     0     0  ...     0   
65545     0     1     1     0     0     1     0     0     0     0  ...     0   
65546     0     1     1     0     0     0     1     0     0     0  ...     1   

       c10_0  c10_1  c10_2  c10_3  c10_4  c10_5  c10_6  c10_7  win  
0          0      0      0      0      0      1      0      1    1  
1          0      0      0      0      1      1      0      1    1  
2          1      0      0      1      0      1      1      0    1  
3          1      0      0      1      0      1      1      1    0  
4          0      1      0      1      1      0      1      1    1  
...      ...    ...    ...    ...    ...    ...    ...    ...  ...  
65542      0      1      1      1      1      1      0      1    1  
65543      0      1      0      1      1      0      1      1    1  
65544      0      1      1      1      0      1      1      0    1  
65545      0      1      0      1      1      0      1      1    0  
65546      0      0      0      1      1      1      0      0    1  

[65547 rows x 81 columns]

#단순인코딩딥러닝

In [64]:
train, test = train_test_split(df,test_size=0.2)
feature = list(df.drop(columns='win').columns)
target = 'win'
X_train = train[feature]
y_train = train[target]
X_test = test[feature]
y_test = test[target]
X_train.shape, y_train.shape, X_test.shape, y_test.shape

((52437, 80), (52437,), (13110, 80), (13110,))

In [83]:
model = tf.keras.models.Sequential([
    tf.keras.layers.Input(shape=80),
    tf.keras.layers.Dense(128, activation='relu'),
    tf.keras.layers.Dense(128, activation='relu'),
    tf.keras. layers.Dense(1, activation='sigmoid')
])
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

model.fit(X_train,y_train,epochs=10)

Epoch 1/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6952 - accuracy: 0.5067
Epoch 2/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6917 - accuracy: 0.5231
Epoch 3/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6896 - accuracy: 0.5316
Epoch 4/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6864 - accuracy: 0.5426
Epoch 5/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6811 - accuracy: 0.5592
Epoch 6/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6732 - accuracy: 0.5775
Epoch 7/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6623 - accuracy: 0.5968
Epoch 8/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6501 - accuracy: 0.6158
Epoch 9/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6358 - accuracy: 0.6339
Epoch 10/10
1639/1639 [==============================] - 2s 1ms/step - loss: 0.621

In [84]:
test_loss, test_acc = model.evaluate(X_test,  y_test, verbose=2)

410/410 - 0s - loss: 0.7516 - accuracy: 0.5123 - 380ms/epoch - 926us/step


#통계뽑아서 딥러닝

In [37]:
df=pd.read_csv('ocdd.csv')
df=df[:65547]
df, test = train_test_split(df,test_size=0.2)
df=df.drop(columns=['matchId'])
df.reset_index(drop=True,inplace=True)
test.reset_index(drop=True,inplace=True)
df

champ1   champ2    champ3       champ4    champ5       champ6  \
0             Gwen   RekSai   Camille         Jhin     Braum       Irelia   
1            Teemo   Graves  Katarina     Aphelios    Maokai       Rumble   
2           Anivia   Rengar     Talon         Jhin       Zoe         Sett   
3            Viego   Lillia     Galio      Caitlyn      Bard     Malphite   
4         Malphite  Shyvana       Lux         Nami   Caitlyn        Yuumi   
...            ...      ...       ...          ...       ...          ...   
52432    TahmKench   Rumble     Yasuo       Lucian      Nami      Trundle   
52433  Mordekaiser   RekSai     Annie  MissFortune    Xerath       Darius   
52434     Renekton    Talon  Vladimir         Ashe      Pyke       Rengar   
52435         Yone      Zac    Kennen         Ashe    Maokai      Camille   
52436         Ornn   LeeSin       Zoe       Samira  Nautilus  Mordekaiser   

             champ7    champ8       champ9     champ10  win  
0             Diana     Yasuo       KogMaw        Lulu    1  
1           XinZhao     Fiora       Lucian  Blitzcrank    0  
2      FiddleSticks      Yone       Ezreal         Lux    1  
3           Kindred     Janna  MissFortune      Viktor    0  
4          Tristana   Camille         Ahri      Gragas    1  
...             ...       ...          ...         ...  ...  
52432        LeeSin       Zoe       Samira       Taric    0  
52433         Poppy  Renekton         Jhin      Anivia    0  
52434        Graves       Vex  MissFortune         Zoe    0  
52435         Talon  Kassadin       Lucian      Thresh    1  
52436       Nidalee    Akshan       Lucian      Soraka    0  

[52437 rows x 11 columns]

In [38]:
#이 챔프의 승률    
#아군 챔프와의 시너지
#적 챔프 상대로 승률
cDict={}
for i in cList:
    cDict[i]=[{},{},0,0]
    for j in [x for x in cList if x!=i]:
        cDict[i][0][j]=[]
        cDict[i][1][j]=[]
     
for i in range(len(df)): #i는 row
    for j in range(1,6): #팀중 한명씩 선택
        for k in [x for x in range(1,6) if x!=j]: #팀의 나머지중 선택
            cDict[df[f'champ{j}'][i]][0][df[f'champ{k}'][i]].append(df['win'][i]) #cDict[우리팀챔피언][팀시너지dict][우리팀다른챔피언]에 1추가
            cDict[df[f'champ{j+5}'][i]][0][df[f'champ{k+5}'][i]].append(int(not df['win'][i])) #cDict[우리팀챔피언][팀시너지dict][우리팀다른챔피언]에 1추가
            
        for k in range(6,11): #적팀 한명씩 선택
            cDict[df[f'champ{j}'][i]][1][df[f'champ{k}'][i]].append(df['win'][i]) #cDict[우리팀챔피언][적카운터dict][적챔피언]에 1추가
            cDict[df[f'champ{j+5}'][i]][1][df[f'champ{k-5}'][i]].append(int(not df['win'][i])) #cDict[우리팀챔피언][적카운터dict][적챔피언]에 1추가
            
    if df['win'][i]==1: #이긴판이면
        cDict[df[f'champ{j}'][i]][2]+=1 #cDict[우리팀챔피언][승리수]에 1추가
        cDict[df[f'champ{j+5}'][i]][3]+=1 #cDict[적팀챔피언][패배수]에 1추가
    else: #진판이면
        cDict[df[f'champ{j}'][i]][3]+=1 #cDict[우리팀챔피언][패배수]에 1추가
        cDict[df[f'champ{j+5}'][i]][2]+=1 #cDict[적팀챔피언][승리수]에 1추가
    
        
for i in cDict: #어떤챔피언
    for j in cDict[i][0]: #다른 어떤 챔피언
        if len(cDict[i][0][j])!=0: #한판이라도 기록이 있으면
            cDict[i][0][j] = sum(cDict[i][0][j])/len(cDict[i][0][j]) #승수/판수
        else: #기록이 없으면
            cDict[i][0][j] = 0.5
    for j in cDict[i][1]:
        if len(cDict[i][1][j])!=0:
            cDict[i][1][j] = sum(cDict[i][1][j])/len(cDict[i][1][j])
        else:
            cDict[i][1][j] = 0.5
cDict['total'] = len(df)
cDict

{'Aatrox': [{'Ahri': 0.5168539325842697,
   'Akali': 0.5100671140939598,
   'Akshan': 0.5102040816326531,
   'Alistar': 0.5327102803738317,
   'Amumu': 0.5185185185185185,
   'Anivia': 0.5619047619047619,
   'Annie': 0.42857142857142855,
   'Aphelios': 0.4425770308123249,
   'Ashe': 0.5616438356164384,
   'AurelionSol': 0.5333333333333333,
   'Azir': 0.4878048780487805,
   'Bard': 0.4794520547945205,
   'Blitzcrank': 0.5013774104683195,
   'Brand': 0.4166666666666667,
   'Braum': 0.5,
   'Caitlyn': 0.49333333333333335,
   'Camille': 0.6296296296296297,
   'Cassiopeia': 0.5223880597014925,
   'Chogath': 0.8333333333333334,
   'Corki': 0.5294117647058824,
   'Darius': 0.5652173913043478,
   'Diana': 0.48314606741573035,
   'DrMundo': 0.3333333333333333,
   'Draven': 0.5625,
   'Ekko': 0.47780678851174935,
   'Elise': 0.5977011494252874,
   'Evelynn': 0.5274725274725275,
   'Ezreal': 0.4819277108433735,
   'FiddleSticks': 0.4642857142857143,
   'Fiora': 0.6,
   'Fizz': 0.5588235294117647,

In [39]:
def f_e(df,cDict):
    for i in range(5):
        for j in range(4):
            k=[x for x in [0,1,2,3,4] if x != i][j]
            df[f'c{i}s{j}']=None
            df[f'c{i}s{j}'] = df.apply(lambda x: cDict[x[f'champ{i+1}']][0][x[f'champ{k+1}']],axis=1)
        for j in range(5):
            df[f'c{i}c{j}']=None
            df[f'c{i}c{j}'] = df.apply(lambda x: cDict[x[f'champ{i+1}']][1][x[f'champ{j+6}']],axis=1)
    for i in range(1,11):
        df[f'cwr{i}']=None
        df[f'cpr{i}']=None
        df[f'cwr{i}'] = df.apply(lambda x: cDict[x[f'champ{i}']][2]/(cDict[x[f'champ{i}']][2]+cDict[x[f'champ{i}']][3]),axis=1)
        df[f'cpr{i}'] = df.apply(lambda x: (cDict[x[f'champ{i}']][2]+cDict[x[f'champ{i}']][3])/cDict['total'],axis=1)
        df[f'cpr{i}'] = (df[f'cpr{i}']-np.min(df[f'cpr{i}']))/(np.max(df[f'cpr{i}'])-np.min(df[f'cpr{i}']))
        
    for i in range(1,11):
        df=df.drop(columns=f'champ{i}')
    return df

In [40]:
df = f_e(df,cDict)
test = f_e(test,cDict)
df

win      c0s0      c0s1      c0s2      c0s3      c0c0      c0c1  \
0        1  0.557377  0.444444  0.476965  0.475000  0.490741  0.500000   
1        0  0.552147  0.514563  0.433673  0.522936  0.509259  0.490741   
2        1  0.608696  0.508929  0.524051  0.571429  0.591837  0.454545   
3        0  0.554348  0.523490  0.505376  0.528846  0.522936  0.442308   
4        1  0.333333  0.504545  0.444444  0.475309  0.542601  0.512821   
...    ...       ...       ...       ...       ...       ...       ...   
52432    0  0.368421  0.516667  0.503846  0.467626  0.510204  0.507246   
52433    0  0.515152  0.500000  0.376471  0.431818  0.357143  0.415730   
52434    0  0.535168  0.436364  0.435897  0.497835  0.528736  0.490506   
52435    1  0.459770  0.534979  0.500000  0.496644  0.476861  0.480730   
52436    0  0.505618  0.470588  0.485714  0.529412  0.457143  0.506250   

           c0c2      c0c3      c0c4  ...      cwr6      cpr6      cwr7  \
0      0.458333  0.600000  0.459893  ...  0.520000  0.013070  0.500000   
1      0.475806  0.498113  0.469298  ...  0.514286  0.007129  0.441860   
2      0.492958  0.444444  0.484127  ...  0.482684  0.049471  0.517007   
3      0.594937  0.448598  0.561404  ...  0.504348  0.011990  0.542857   
4      0.451977  0.431373  0.511628  ...  0.467214  0.722726  0.409091   
...         ...       ...       ...  ...       ...       ...       ...   
52432  0.420561  0.549180  0.368421  ...  0.463504  0.029164  0.470085   
52433  0.470588  0.440217  0.470588  ...  0.500000  0.005185  0.529297   
52434  0.484716  0.471178  0.477366  ...  0.525000  0.003889  0.533784   
52435  0.411765  0.533011  0.472669  ...  0.424242  0.010261  0.480000   
52436  0.415094  0.473958  0.400000  ...  0.391304  0.002052  0.489796   

           cpr7      cwr8      cpr8      cwr9      cpr9     cwr10     cpr10  
0      0.003672  0.459677  0.012962  0.583333  0.000864  0.510532  0.753402  
1      0.004213  0.545455  0.007885  0.492611  0.021495  0.522699  0.768092  
2      0.015446  0.495575  0.011774  0.438298  0.024951  0.497215  0.426226  
3      0.003348  0.507273  0.118384  0.400844  0.025167  0.454545  0.003132  
4      0.001944  0.424242  0.010261  0.539683  0.006373  0.492537  0.071938  
...         ...       ...       ...       ...       ...       ...       ...  
52432  0.024843  0.508982  0.017606  0.495798  0.012422  0.518265  0.046878  
52433  0.054871  0.393939  0.006697  0.496795  0.033269  0.498471  0.034889  
52434  0.015554  0.423684  0.040614  0.400844  0.025167  0.508982  0.017606  
52435  0.007669  0.333333  0.002160  0.492611  0.021495  0.497409  1.000000  
52436  0.010153  0.785714  0.002592  0.492611  0.021495  0.525221  0.207280  

[52437 rows x 66 columns]

In [123]:
df.to_csv(os.path.join(os.getcwd(),r'ocdd_FE.csv'), encoding='utf-8',index=False)
test.to_csv(os.path.join(os.getcwd(),r'ocdd_FE_test.csv'), encoding='utf-8',index=False)

#통계분석

In [21]:
df = pd.read_csv('ocdd_FE.csv')
test = pd.read_csv('ocdd_FE_test.csv')

In [41]:
profile = ProfileReport(df, minimal=True).to_notebook_iframe()

Render HTML: 100%|██████████| 1/1 [00:02<00:00,  2.15s/it]


In [58]:
feature = list(df.drop(columns='win').columns)
target = 'win'
X_train = df[feature]
y_train = df[target]
X_test = test[feature]
y_test = test[target]
X_train.shape, y_train.shape, X_test.shape, y_test.shape

((52437, 65), (52437,), (13110, 65), (13110,))

In [59]:
model = tf.keras.models.Sequential([
    tf.keras.layers.Input(shape=65),
    tf.keras.layers.Dense(32, activation='relu'),
    tf.keras.layers.Dense(32, activation='relu'),
    tf.keras. layers.Dense(1, activation='sigmoid')
])
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

model.fit(X_train,y_train,epochs=25)

Epoch 1/25
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6838 - accuracy: 0.5477
Epoch 2/25
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6582 - accuracy: 0.5985
Epoch 3/25
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6468 - accuracy: 0.6160
Epoch 4/25
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6417 - accuracy: 0.6241
Epoch 5/25
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6383 - accuracy: 0.6266
Epoch 6/25
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6348 - accuracy: 0.6331
Epoch 7/25
1639/1639 [==============================] - 2s 1ms/step - loss: 0.6327 - accuracy: 0.6363
Epoch 8/25
1639/1639 [==============================] - 2s 939us/step - loss: 0.6303 - accuracy: 0.6361
Epoch 9/25
1639/1639 [==============================] - 1s 890us/step - loss: 0.6294 - accuracy: 0.6392
Epoch 10/25
1639/1639 [==============================] - 1s 908us/step - loss:

In [60]:
test_loss, test_acc = model.evaluate(X_test,  y_test, verbose=2)

410/410 - 0s - loss: 0.7370 - accuracy: 0.5252 - 302ms/epoch - 736us/step


In [61]:
def model_builder(hp):
    model = tf.keras.models.Sequential()
    model.add(tf.keras.layers.Input(shape=65))

    # 첫 번째 Dense layer에서 노드 수를 조정(32-512)합니다.
    hp_units = hp.Int('units', min_value = 32, max_value = 512, step = 32)
    model.add(tf.keras.layers.Dense(units = hp_units, activation = tf.keras.layers.LeakyReLU(alpha=0.1)))
    model.add(tf.keras.layers.Dense(1, activation='sigmoid'))

    # Optimizer의 학습률(learning rate)을 조정[0.01, 0.001, 0.0001]합니다. 
    hp_learning_rate = hp.Choice('learning_rate', values = [1e-2, 1e-3, 1e-4]) 
    model.compile(optimizer = tf.keras.optimizers.Adam(learning_rate = hp_learning_rate),
                loss = tf.keras.losses.BinaryCrossentropy(), 
                metrics = ['accuracy'])
                
    return model

In [62]:
tuner = kt.Hyperband(model_builder,
                     objective = 'val_accuracy', 
                     max_epochs = 50, # 일반적으로 10, 빠른 구현을 위해서 숫자를 줄였음.
                     factor = 3,
                     directory = 'my_dir',
                     project_name = 'b')

In [63]:
class ClearTrainingOutput(tf.keras.callbacks.Callback):
  def on_train_end(*args, **kwargs):
    IPython.display.clear_output(wait = True)

In [64]:
tuner.search(X_train, y_train, epochs = 50, validation_data = (X_test, y_test), callbacks = [ClearTrainingOutput()])

# Get the optimal hyperparameters
best_hps = tuner.get_best_hyperparameters(num_trials = 1)[0]

print(f"""
하이퍼 파라미터 검색이 완료되었습니다. 
최적화된 첫 번째 Dense 노드 수는 {best_hps.get('units')} 입니다.
최적의 학습 속도는 {best_hps.get('learning_rate')} 입니다.
""")

Trial 63 Complete [00h 00m 26s]
val_accuracy: 0.5207475423812866

Best val_accuracy So Far: 0.5319603085517883
Total elapsed time: 00h 19m 07s
INFO:tensorflow:Oracle triggered exit

하이퍼 파라미터 검색이 완료되었습니다. 
최적화된 첫 번째 Dense 노드 수는 448 입니다.
최적의 학습 속도는 0.01 입니다.



In [65]:
# 최적의 하이퍼 파라미터를 사용하여 모델을 구축하고 데이터에 대해 교육
model = tuner.hypermodel.build(best_hps)
model.summary()

Model: "sequential_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_2 (Dense)             (None, 448)               29568     
                                                                 
 dense_3 (Dense)             (None, 1)                 449       
                                                                 
Total params: 30,017
Trainable params: 30,017
Non-trainable params: 0
_________________________________________________________________


In [66]:
model.fit(X_train, y_train, epochs = 50, validation_data = (X_test, y_test))


Epoch 1/50
1639/1639 [==============================] - 4s 2ms/step - loss: 0.6979 - accuracy: 0.5277 - val_loss: 0.6958 - val_accuracy: 0.5189
Epoch 2/50
1639/1639 [==============================] - 3s 2ms/step - loss: 0.6670 - accuracy: 0.5894 - val_loss: 0.7179 - val_accuracy: 0.5201
Epoch 3/50
1639/1639 [==============================] - 6s 4ms/step - loss: 0.6545 - accuracy: 0.6101 - val_loss: 0.8020 - val_accuracy: 0.5154
Epoch 4/50
1639/1639 [==============================] - 5s 3ms/step - loss: 0.6514 - accuracy: 0.6154 - val_loss: 0.7405 - val_accuracy: 0.5232
Epoch 5/50
1639/1639 [==============================] - 5s 3ms/step - loss: 0.6457 - accuracy: 0.6187 - val_loss: 0.7346 - val_accuracy: 0.5231
Epoch 6/50
1639/1639 [==============================] - 4s 3ms/step - loss: 0.6438 - accuracy: 0.6248 - val_loss: 0.7300 - val_accuracy: 0.5259
Epoch 7/50
1639/1639 [==============================] - 4s 2ms/step - loss: 0.6436 - accuracy: 0.6226 - val_loss: 0.7998 - val_accuracy:

In [67]:
test_loss, test_acc = model.evaluate(X_test,  y_test, verbose=2)

410/410 - 0s - loss: 0.7607 - accuracy: 0.5257 - 389ms/epoch - 949us/step


In [68]:
import matplotlib.pyplot as plt
from sklearn.pipeline import make_pipeline
from xgboost import XGBClassifier
from sklearn.model_selection import RandomizedSearchCV
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import roc_auc_score
from sklearn.metrics import roc_curve

In [69]:
#CV
dists = {
    'xgbclassifier__max_depth': range(5,10),
    }
pipe = make_pipeline(
    XGBClassifier(n_estimators=200
                  , random_state=2
                  , n_jobs=-1
                  , learning_rate=0.2
    )
)
    
clf = RandomizedSearchCV(
    pipe, 
    param_distributions=dists, 
    n_iter=50, 
    cv=3,
    scoring='f1',
    verbose=1,
    n_jobs=-1
)
clf.fit(X_train, y_train);

y_pred = clf.predict(X_test)
print('정확도: ', accuracy_score(y_test, y_pred))
print('최적 하이퍼파라미터: ', clf.best_params_)
print('f1: ', clf.best_score_)
print(classification_report(y_pred, y_test))

C:\Users\gram\anaconda3\envs\Project_5\lib\site-packages\sklearn\model_selection\_search.py:292: UserWarning: The total space of parameters 5 is smaller than n_iter=50. Running 5 iterations. For exhaustive searches, use GridSearchCV.
  warnings.warn(


Fitting 3 folds for each of 5 candidates, totalling 15 fits


C:\Users\gram\anaconda3\envs\Project_5\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[10:21:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.0/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
정확도:  0.5203661327231122
최적 하이퍼파라미터:  {'xgbclassifier__max_depth': 5}
f1:  0.6637876725172306
              precision    recall  f1-score   support

           0       0.52      0.52      0.52      6507
           1       0.52      0.52      0.52      6603

    accuracy                           0.52     13110
   macro avg       0.52      0.52      0.52     13110
weighted avg       0.52      0.52      0.52     13110



In [70]:

y_pred_proba = clf.predict_proba(X_test)[:, 1]
fpr, tpr, thresholds = roc_curve(y_test, y_pred_proba)

roc = pd.DataFrame({
    'FPR(Fall-out)': fpr, 
    'TPRate(Recall)': tpr, 
    'Threshold': thresholds
})

plt.scatter(fpr, tpr)
plt.title('ROC curve')
plt.xlabel('FPR(Fall-out)')
plt.ylabel('TPR(Recall)');
print(roc.head())

# threshold 최대값의 인덱스, np.argmax()
optimal_idx = np.argmax(tpr - fpr)
optimal_threshold = thresholds[optimal_idx]
print('idx:', optimal_idx, ', threshold:', optimal_threshold)

y_pred_optimal = y_pred_proba >= optimal_threshold
print(classification_report(y_test, y_pred_optimal))
print('예측 정확도: ', accuracy_score(y_test, y_pred_optimal))
print(roc_auc_score(y_test,y_pred_optimal))

   FPR(Fall-out)  TPRate(Recall)  Threshold
0       0.000000        0.000000   1.997618
1       0.000153        0.000000   0.997618
2       0.000306        0.000000   0.996448
3       0.000306        0.000914   0.990218
4       0.000611        0.000914   0.988312
idx: 3388 , threshold: 0.49009734
              precision    recall  f1-score   support

           0       0.52      0.50      0.51      6545
           1       0.52      0.54      0.53      6565

    accuracy                           0.52     13110
   macro avg       0.52      0.52      0.52     13110
weighted avg       0.52      0.52      0.52     13110

예측 정확도:  0.5215102974828375
0.5214746232218568


In [71]:
pipe2 = make_pipeline(
    XGBClassifier(n_estimators=200
                  , random_state=2
                  , n_jobs=-1
                  , learning_rate=0.2
                  , max_depth=9
    )
)
pipe2.fit(X_train,y_train);
rf = pipe2['xgbclassifier']
importances = pd.Series(rf.feature_importances_, X_train.columns)
n = 20
plt.figure(figsize=(10,n/2))
plt.title(f'Top {n} features')
importances.sort_values()[-n:].plot.barh();

C:\Users\gram\anaconda3\envs\Project_5\lib\site-packages\xgboost\sklearn.py:1224: UserWarning: The use of label encoder in XGBClassifier is deprecated and will be removed in a future release. To remove this warning, do the following: 1) Pass option use_label_encoder=False when constructing XGBClassifier object; and 2) Encode your labels (y) as integers starting with 0, i.e. 0, 1, 2, ..., [num_class - 1].
  warnings.warn(label_encoder_deprecation_msg, UserWarning)


[10:21:30] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.5.0/src/learner.cc:1115: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
